In [17]:
import os
import re

from solidity_parser import parser
from tqdm import tqdm


class SolidityObfuscator:
    """
    A class to obfuscate variable, function, and contract names in Solidity files.
    """

    def __init__(self):
        self.name_mapping = {}
        self.counters = {
            'contract': 1,
            'function': 1,
            'state_variable': 1,
            'local_variable': 1
        }
        print("Initialized SolidityObfuscator.")

    def _get_placeholder(self, kind):
        """
        Generates a unique placeholder for the given kind of identifier.
        """
        placeholder = f"{kind}_{self.counters[kind]}"
        print(f"Generated placeholder '{placeholder}' for kind '{kind}'.")
        self.counters[kind] += 1
        return placeholder

    @staticmethod
    def remove_pragma_directive(content):
        """
        Removes the pragma directive from the Solidity code.
        """
        print("Removing pragma directives...")
        pragma_pattern = re.compile(r'^\s*pragma\s+solidity\s+[^;]+;\s*$', re.MULTILINE)
        content_no_pragma = re.sub(pragma_pattern, '', content)
        return content_no_pragma

    @staticmethod
    def remove_comments(content):
        """
        Removes single-line (//) and multi-line (/* */) comments from the Solidity code.
        """
        print("Removing comments...")
        comment_pattern = re.compile(r'//.*?$|/\*.*?\*/', re.DOTALL | re.MULTILINE)
        content_no_comments = re.sub(comment_pattern, '', content)
        return content_no_comments

    def obfuscate_file(self, input_path, output_path):
        """
        Obfuscates the given Solidity file and saves the obfuscated content to an output file.
        """
        print(f"Starting obfuscation for file: {input_path}")
        if not os.path.isfile(input_path):
            raise FileNotFoundError(f"Input file not found: {input_path}")

        try:
            with open(input_path, 'r', encoding='utf-8') as file:
                content = file.read()
            if not content.strip():
                raise ValueError("Input file is empty.")
            print("Successfully read input file.")

            # Remove comments and pragma directive
            content = self.remove_comments(content)
            content = self.remove_pragma_directive(content)

            # Parse the Solidity code into an AST
            print("Parsing Solidity file to AST...")
            ast = parser.parse_file(input_path, loc=False)
            print("AST successfully generated.")
            print(f"Initial AST: {ast}\n")

            self._process_ast(ast)

            print(f"Identifier mappings generated: {self.name_mapping}")

            # Perform replacements using a single regex
            content = self._replace_identifiers(content)
            print("Replacements applied successfully.")

            # Write obfuscated content to the output file
            with open(output_path, 'w', encoding='utf-8') as file:
                file.write(content)
            print(f"Obfuscation complete: {output_path}")

        except Exception as e:
            print(f"Error processing file {input_path}: {e}")
            raise

    def _process_ast(self, ast):
        """
        Processes the AST to identify and map identifiers.
        """
        print("Processing AST to identify identifiers...")
        stack = [(ast, None)]  # (current_node, parent_type)
        while stack:
            node, parent_type = stack.pop()

            if isinstance(node, dict):
                # Extract identifier names, ignoring None names
                if 'name' in node and 'type' in node:
                    name = node['name']
                    if name is not None:  # Skip None names
                        kind = self._determine_kind(node, parent_type)
                        if kind and name not in self.name_mapping:
                            placeholder = self._get_placeholder(kind)
                            self.name_mapping[name] = placeholder
                            print(f"Mapped '{name}' to '{placeholder}' (kind: {kind}).")
                    else:
                        print(f"Warning: Encountered node with None name, type: {node.get('type')}")

                # Traverse child nodes
                for key, value in node.items():
                    if isinstance(value, (dict, list)):
                        stack.append((value, node.get('type')))

            elif isinstance(node, list):
                for item in node:
                    stack.append((item, parent_type))
        print("Finished processing AST.\n")

    @staticmethod
    def _determine_kind(node, parent_type):
        """
        Determines the kind of identifier based on its parent type in the AST.
        """
        if parent_type == 'ContractDefinition':
            return 'contract'
        elif parent_type == 'FunctionDefinition':
            return 'function'
        elif parent_type == 'StateVariableDeclaration':
            return 'state_variable'
        elif parent_type in ('VariableDeclaration', 'ParameterList'):
            return 'local_variable'
        return None

    def _replace_identifiers(self, content):
        """
        Replaces all identified names in the content using a single-pass regex.
        """
        print("Replacing identifiers in the Solidity code...")
        # Build a single regex for all replacements
        pattern = re.compile(r'\b(' + '|'.join(re.escape(name) for name in self.name_mapping.keys()) + r')\b')
        replaced_content = pattern.sub(lambda match: self.name_mapping[match.group(0)], content)
        print("Replacement complete.")
        return replaced_content

    def obfuscate_multiple_files(self, file_paths, output_dir):
        """
        Processes multiple Solidity files and saves obfuscated versions to the output directory.
        """
        os.makedirs(output_dir, exist_ok=True)
        print(f"Processing multiple files. Output directory: {output_dir}")
        for file_path in tqdm(file_paths):
            try:
                file_name = os.path.basename(file_path)
                output_path = os.path.join(output_dir, f"obfuscated_{file_name}")
                print(f"\nProcessing file: {file_path}")
                self.obfuscate_file(file_path, output_path)
            except Exception as e:
                print(f"Skipping {file_path} due to error: {e}")


# Usage Example
if __name__ == "__main__":
    input_file = "example.sol"  # Replace with the actual file path
    output_file = "example_obfuscated.sol"

    print("Starting Solidity Obfuscator...")
    obfuscator = SolidityObfuscator()

    # try:
    #     obfuscator.obfuscate_file(input_file, output_file)
    # except Exception as e:
    #     print(f"Failed to obfuscate file: {e}")

    path_to_files = os.path.join("..", "dataset", "manually-verified-tiny-test", "source", "safe")
    input_files = [os.path.join(path_to_files, file_name) for file_name in os.listdir(path_to_files)]
    output_directory = "obfuscated_output"
    obfuscator.obfuscate_multiple_files(input_files, output_directory)


Starting Solidity Obfuscator...
Initialized SolidityObfuscator.
Processing multiple files. Output directory: obfuscated_output


  0%|          | 0/101 [00:00<?, ?it/s]


Processing file: ../dataset/manually-verified-tiny-test/source/safe/0x0a3ec7050884f00b5d9b11131de59dced0fafedb.sol
Starting obfuscation for file: ../dataset/manually-verified-tiny-test/source/safe/0x0a3ec7050884f00b5d9b11131de59dced0fafedb.sol
Successfully read input file.
Removing comments...
Removing pragma directives...
Parsing Solidity file to AST...


  1%|          | 1/101 [00:00<01:36,  1.03it/s]

Error processing file ../dataset/manually-verified-tiny-test/source/safe/0x0a3ec7050884f00b5d9b11131de59dced0fafedb.sol: unrecognized expression
Skipping ../dataset/manually-verified-tiny-test/source/safe/0x0a3ec7050884f00b5d9b11131de59dced0fafedb.sol due to error: unrecognized expression

Processing file: ../dataset/manually-verified-tiny-test/source/safe/0x0a1bb328061a2463db94116612d8eb289672ac68.sol
Starting obfuscation for file: ../dataset/manually-verified-tiny-test/source/safe/0x0a1bb328061a2463db94116612d8eb289672ac68.sol
Successfully read input file.
Removing comments...
Removing pragma directives...
Parsing Solidity file to AST...


...

AST successfully generated.
Initial AST: {'type': 'SourceUnit', 'children': [{'type': 'PragmaDirective', 'name': 'solidity', 'value': '>=0.4.24<0.8.0'}, {'type': 'ContractDefinition', 'name': 'Initializable', 'baseContracts': [], 'subNodes': [{'type': 'StateVariableDeclaration', 'variables': [{'type': 'VariableDeclaration', 'typeName': {'type': 'ElementaryTypeName', 'name': 'bool'}, 'name': '_initialized', 'expression': None, 'visibility': 'private', 'isStateVar': True, 'isDeclaredConst': False, 'isIndexed': False}], 'initialValue': None}, {'type': 'StateVariableDeclaration', 'variables': [{'type': 'VariableDeclaration', 'typeName': {'type': 'ElementaryTypeName', 'name': 'bool'}, 'name': '_initializing', 'expression': None, 'visibility': 'private', 'isStateVar': True, 'isDeclaredConst': False, 'isIndexed': False}], 'initialValue': None}, {'type': 'ModifierDefinition', 'name': 'initializer', 'parameters': {'type': 'ParameterList', 'parameters': []}, 'body': {'type': 'Block', 'statements

 99%|█████████▉| 100/101 [00:26<00:00,  5.51it/s]

Replacement complete.
Replacements applied successfully.
Obfuscation complete: obfuscated_output/obfuscated_0x0a6f0c541be542c098b7ee03c9c634f20bcf8422.sol

Processing file: ../dataset/manually-verified-tiny-test/source/safe/0x0a2ea71d943bf917b410593194595e1f48d40e54.sol
Starting obfuscation for file: ../dataset/manually-verified-tiny-test/source/safe/0x0a2ea71d943bf917b410593194595e1f48d40e54.sol
Successfully read input file.
Removing comments...
Removing pragma directives...
Parsing Solidity file to AST...


100%|██████████| 101/101 [00:28<00:00,  3.58it/s]

AST successfully generated.
Initial AST: {'type': 'SourceUnit', 'children': [{'type': 'PragmaDirective', 'name': 'solidity', 'value': '^0.4.21'}, {'type': 'ContractDefinition', 'name': 'REPOPAccessControl', 'baseContracts': [], 'subNodes': [{'type': 'StateVariableDeclaration', 'variables': [{'type': 'VariableDeclaration', 'typeName': {'type': 'ElementaryTypeName', 'name': 'address'}, 'name': 'ceoAddress', 'expression': None, 'visibility': 'public', 'isStateVar': True, 'isDeclaredConst': False, 'isIndexed': False}], 'initialValue': None}, {'type': 'StateVariableDeclaration', 'variables': [{'type': 'VariableDeclaration', 'typeName': {'type': 'ElementaryTypeName', 'name': 'address'}, 'name': 'cfoAddress', 'expression': None, 'visibility': 'public', 'isStateVar': True, 'isDeclaredConst': False, 'isIndexed': False}], 'initialValue': None}, {'type': 'StateVariableDeclaration', 'variables': [{'type': 'VariableDeclaration', 'typeName': {'type': 'ElementaryTypeName', 'name': 'address'}, 'name':